# PIRA Link Prediction

In [4]:
import pandas as pd
import numpy as np
import re
import networkx as nx
from datetime import datetime
import matplotlib.pyplot as plt
import itertools
import time
pd.set_option('display.max_rows', 1500)
pd.set_option('display.max_columns', 1000)
pd.set_option('display.width', 1000)

### Create Edge List from 6 Matrix files
#### The last 3 time steps are set as test edges

In [5]:
df_1 = pd.read_csv('60_PERIOD1_NET.csv')
df_1.shape

(334, 335)

In [6]:
df_1

Unnamed: 0  ZF1013  ZF1014  ZF1015  ZF1020  ZF1025  ZF1029  ZF1031  ZF1032  ZF1038  ZF104  ZF1049  ZF105  ZF1059  ZF1060  ZF107  ZF1078  ZF1079  ZF1082  ZF1088  ZF1089  ZF1091  ZF1101  ZF1103  ZF1116  ZF1118  ZF1122  ZF1127  ZF1128  ZF1129  ZF1132  ZF1134  ZF1135  ZF1138  ZF1149  ZF1151  ZF1157  ZF1158  ZF1161  ZF1162  ZF1163  ZF1170  ZF1173  ZF1174  ZF1177  ZF118  ZF1181  ZF1182  ZF1183  ZF119  ZF1194  ZF1201  ZF1203  ZF1204  ZF1210  ZF1215  ZF1220  ZF1226  ZF1227  ZF123  ZF1240  ZF1248  ZF1249  ZF1251  ZF1252  ZF1259  ZF1261  ZF1264  ZF1266  ZF1269  ZF1271  ZF1277  ZF129  ZF1294  ZF1302  ZF1304  ZF1318  ZF1320  ZF1322  ZF1328  ZF133  ZF1335  ZF1338  ZF1340  ZF1341  ZF1343  ZF1356  ZF1365  ZF1366  ZF1367  ZF1377  ZF1379  ZF1380  ZF140  ZF143  ZF15  ZF151  ZF152  ZF154  ZF155  ZF156  ZF157  ZF164  ZF172  ZF176  ZF190  ZF194  ZF195  ZF197  ZF20  ZF206  ZF208  ZF213  ZF214  ZF217  ZF219  ZF222  ZF237  ZF24  ZF248  ZF251  ZF257  ZF260  ZF261  ZF267  ZF268  ZF273  ZF276  ZF28  ZF287  \
0       ZF1013       0       0       0       0       0       0       0       0       0      0       0      0       0       0      0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       1       0       0       0       0       0       0       0       0       0       0       0       0      0       0       0       0      1       0       0       0       0       0       0       0       0       0      0       0       0       0       0       0       0       0       0       0       0       0       0      0       0       0       1       0       0       0       0      0       0       0       0       0       0       0       0       0       0       0       0       0      0      0     0      0      0      0      0      0      0      0      0      0      0      0      0      0     0      0      0      0      0      0      0      0      0     0      0      0      0      0      0      0      0      0      0     0      0   
1       ZF1014       0       0       0       0       0       0       0       0       0      0       0      0       0       0      0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0      0       0       0       0      0       0       0       0       0       0       0       0       0       0      0       0       0       0       0       0       0       0       0       0       0       0       0      0       0       0       0       0       0       0       0      0       0       0       0       0       0       0       0       0       0       0       0       0      0      0     0      0      0      0      0      0      0      0      0      0      0      0      0      0     0      0      0      0      0      0      0      0      0     0      0      0      0      1      0      0      0      0      0     0      0   
2       ZF1015       0       0       0       0       0       0       0       0       0      0       0      0       0       0      0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       0       1      0       0       0       0      0       0       0       0       0       0       0       0       0       0      0       0       0       0       0       0       0       0       0       0       0       0       0      0       0       0       0       0       0       0       0      0       0       0       0       0       0       0       0       0       0       0       0       0      0      0     0      0      0      0      0      0      0      0      0      0      0      0      0      0     0      0      0      0      0      0      0      0      1     0      0      0      0      0      0      0      0      0      0     0      0   


In [7]:
##resolve matrix
df = pd.DataFrame(columns = ['Source', 'Target', 'Weight', 'Year'])
#df = df.astype('int32')

In [8]:
def fetch_edge_list(df, data_year, year):
    done = []
    for i, row in data_year.iterrows(): 
        x = row['Unnamed: 0']
        for c in data_year.columns:
            # if not the source column and not unconnected
            if not c == 'Unnamed: 0' and not row[c] == 0 and c not in done: 
                #if not already in edges
                if df[(df['Source'] == x ) & (df['Target'] == c)].shape[0] == 0: 
                    df = df.append(pd.DataFrame({'Source': x, 'Target': c, 'Weight':row[c], 'Year': year}, index = [0]), ignore_index = True)
                else:
                    #if in edges
                    print('changed_edge')
                    if not (df[(df['Source'] == x ) & (df['Target'] == c)].iloc[0]['Weight'] == row[c]):
                        print(x, c, row[c],(df[(df['Source'] == x ) & (df['Target'] == c)].iloc[0]['Weight'] ))
                    df.loc[(df['Source'] == x ) & (df['Target'] == c), 'Weight'] = row[c]
        done.append(x)
                    
    return df

In [9]:
def fetch_test_edge_list(df, data_year, year, nodes = None):
    
    done = []
    for i, row in data_year.iterrows(): 
        x = row['Unnamed: 0']
        for c in data_year.columns:
            # if not the source column and not unconnected
            if not c == 'Unnamed: 0' and not row[c] == 0 and c not in done and c in nodes and x in nodes: 
                if df[(df['Source'] == x ) & (df['Target'] == c)].shape[0] == 0: 
                    df = df.append(pd.DataFrame({'Source': x, 'Target': c, 'Weight':row[c], 'Year': year}, index = [0]), ignore_index = True)
                else:
                    print('changed_edge')
                    if not (df[(df['Source'] == x ) & (df['Target'] == c)].iloc[0]['Weight'] == row[c]):
                        print(x, c, row[c],(df[(df['Source'] == x ) & (df['Target'] == c)].iloc[0]['Weight'] ))
                    df.loc[(df['Source'] == x ) & (df['Target'] == c), 'Weight'] = row[c]
        done.append(x)
                    
    return df

In [10]:
df = fetch_edge_list(df, df_1, 1)

In [11]:
print(df.shape)
l = list(df['Source'].unique())
l.extend(df['Target'].unique())
l = set(l)
print(len(l))

(405, 4)
334


In [12]:
df_2 = pd.read_csv('60_PERIOD2_NET.csv')
df_2.shape
df = fetch_edge_list(df, df_2, 2)

changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge

In [13]:
print(df.shape)
l = list(df['Source'].unique())
l.extend(df['Target'].unique())
l = set(l)
print(len(l))

(627, 4)
455


In [14]:
df_3 = pd.read_csv('60_PERIOD3_NET.csv')
df_3.shape
df = fetch_edge_list(df, df_3, 3)

changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge

In [15]:
print(df.shape)
l = list(df['Source'].unique())
l.extend(df['Target'].unique())
l = set(l)
print(len(l))

(1464, 4)
768


In [16]:
# save the dataframe so far as train period
train_df = df.copy()

In [17]:
df_4 = pd.read_csv('60_PERIOD4_5_NET.csv')
df_4.shape
df = fetch_test_edge_list(df, df_4, 4, nodes =l)

changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge

In [18]:
print(df.shape)
l = list(df['Source'].unique())
l.extend(df['Target'].unique())
l = set(l)
print(len(l))

(1526, 4)
768


In [19]:
df_6 = pd.read_csv('60_PERIOD6_NET.csv')
df_6.shape
df = fetch_test_edge_list(df, df_6, 6, nodes = l)

changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge
changed_edge


In [20]:
print(df.shape)
l = list(df['Source'].unique())
l.extend(df['Target'].unique())
l = set(l)
print(len(l))

(1554, 4)
768


### Save edge list for visualisation

In [19]:
train_df.to_excel('PIRA_train_edges.xlsx')

In [20]:
df.to_excel('PIRA_edges.xlsx')

### Make training graphs

In [21]:
train_df.columns

Index(['Source', 'Target', 'Weight', 'Year'], dtype='object')

In [22]:
train_g = nx.from_pandas_edgelist(train_df, source='Source', target='Target', edge_attr=['Weight', 'Year'])


In [23]:
g = nx.from_pandas_edgelist(df, source='Source', target='Target', edge_attr=['Weight', 'Year'])


In [24]:
degreees = [t[1] for t in train_g.degree]
degreees
np.mean(degreees)

3.8125

In [25]:
len(train_g.nodes)

768

## Find labelled examples

In [26]:
from networkx.classes.function import non_neighbors
temp = nx.Graph(g)
pairs_df = pd.DataFrame()
p1 = []; p2 = []
for n in temp.nodes:
    for p in non_neighbors(temp, n):
        p1.append(n)
        p2.append(p)
    temp = nx.Graph(temp)
    temp.remove_node(n)

In [27]:
pairs_df['Node1'] = p1
pairs_df['Node2'] = p2
pairs_df['y'] = False
len(pairs_df)

292974

In [28]:
pairs_df

Node1   Node2      y
0       ZF1013  ZF1014  False
1       ZF1013   ZF260  False
2       ZF1013   ZF459  False
3       ZF1013   ZF659  False
4       ZF1013   ZF769  False
...        ...     ...    ...
292969   ZF768   ZF814  False
292970   ZF768   ZF961  False
292971   ZF777   ZF814  False
292972   ZF777   ZF961  False
292973   ZF814   ZF961  False

[292974 rows x 3 columns]

In [29]:
from networkx.classes.function import neighbors
temp = nx.Graph(g)
pairs_df2 = pd.DataFrame()
p1 = []; p2 = [] 
for n in temp.nodes:
    for p in neighbors(temp, n):
        p1.append(n)
        p2.append(p)
    temp = nx.Graph(temp)
    temp.remove_node(n)
pairs_df2['Node1'] = p1
pairs_df2['Node2'] = p2
pairs_df2['y'] = True

In [30]:
pairs_df2

Node1   Node2     y
0     ZF1013  ZF1135  True
1     ZF1013   ZF119  True
2     ZF1013  ZF1304  True
3     ZF1013   ZF629  True
4     ZF1135   ZF119  True
...      ...     ...   ...
1549   ZF668   ZF970  True
1550   ZF685   ZF750  True
1551   ZF717   ZF921  True
1552   ZF731   ZF761  True
1553   ZF741   ZF875  True

[1554 rows x 3 columns]

In [31]:
pairs_df = pd.concat([pairs_df, pairs_df2])

In [32]:
pairs_df

Node1   Node2      y
0     ZF1013  ZF1014  False
1     ZF1013   ZF260  False
2     ZF1013   ZF459  False
3     ZF1013   ZF659  False
4     ZF1013   ZF769  False
...      ...     ...    ...
1549   ZF668   ZF970   True
1550   ZF685   ZF750   True
1551   ZF717   ZF921   True
1552   ZF731   ZF761   True
1553   ZF741   ZF875   True

[294528 rows x 3 columns]

## Create features from training edges

In [33]:
l = list(df['Source'].unique())
l.extend(df['Target'].unique())
l = set(l)

In [34]:
len(l)

768

In [35]:
nodes = pd.DataFrame()
nodes['Node'] = list(l)

### Feature: Sum of Papers

In [36]:
# sum of papers 
sum_papers = []; sum_papers2 =[]
for i, row in nodes.iterrows():
    #get all edges in which row[node] is in
    temp = train_df[(train_df['Source'] == row['Node']) | (train_df['Target'] == row['Node'])]
    sum_papers.append(sum(temp['Weight']))
    sum_papers2.append(sum(temp['Weight'])/temp.shape[0])#only if weights differ from one

In [37]:
nodes['Sum of Papers'] = sum_papers

In [38]:
nodes['Sum of Papers normalised'] = sum_papers2

In [39]:
nodes

Node  Sum of Papers  Sum of Papers normalised
0    ZF1198              3                       1.0
1     ZF853              5                       1.0
2    ZFM658              2                       1.0
3     ZF731              1                       1.0
4    ZF1356              5                       1.0
5     ZF223              3                       1.0
6     ZF734              3                       1.0
7    ZF1357              1                       1.0
8    ZFM539              8                       1.0
9    ZF1343              2                       1.0
10    ZF678             13                       1.0
11   ZF1058              2                       1.0
12     ZF69              3                       1.0
13      ZF6              2                       1.0
14   ZF1000              3                       1.0
15    ZF591              2                       1.0
16     ZF12              7                       1.0
17   ZF1140              2                       1.0
18     ZF32              3                       1.0
19   ZF1166              2                       1.0
20    ZF707              2                       1.0
21   ZF1170              1                       1.0
22    ZF889             14                       1.0
23    ZF706              7                       1.0
24   ZF1365              4                       1.0
25   ZF1302              2                       1.0
26    ZF891              1                       1.0
27   ZF1255              1                       1.0
28   ZF1190              8                       1.0
29   ZFM679              3                       1.0
30    ZF665              6                       1.0
31   ZF1207              8                       1.0
32    ZF837              4                       1.0
33   ZF1262              1                       1.0
34    ZF213              1                       1.0
35    ZF958             12                       1.0
36   ZF1338              1                       1.0
37   ZF1109              6                       1.0
38   ZF1264             11                       1.0
39   ZF1134              1                       1.0
40   ZF1366              1                       1.0
41    ZF738              1                       1.0
42    ZF846              8                       1.0
43   ZF1031              7                       1.0
44    ZF966              4                       1.0
45    ZF445              4                       1.0
46   ZF1348              3                       1.0
47    ZF799              2                       1.0
48    ZF839              1                       1.0
49   ZF1183              4                       1.0
50    ZF983              5                       1.0
51   ZF1359              2                       1.0
52    ZF179              2                       1.0
53    ZF770              4                       1.0
54    ZF542              1                       1.0
55   ZF1211              6                       1.0
56    ZF471              1                       1.0
57    ZF821             10                       1.0
58    ZF682              3                       1.0
59    ZF416              4                       1.0
60    ZF668              1                       1.0
61   ZF1354              5                       1.0
62    ZF164              1                       1.0
63   ZF1087              1                       1.0
64    ZF876              1                       1.0
65     ZF40              5                       1.0
66    ZF407              4                       1.0
67    ZF856              4                       1.0
68   ZF1025              6                       1.0
69   ZF1261              1                       1.0
70    ZF432              9                       1.0
71    ZF350              1                       1.0
72    ZF915              1                       1.0
73    ZF176             18                       1.0
74   ZF1091              1      

### Feature: Sum of Neighbours

In [40]:
from networkx.classes.function import neighbors
temp = nx.Graph(train_g)
sum_neighbours = []

for i, row in nodes.iterrows():
    sum_neighbours.append(temp.degree(row['Node']))


In [41]:
nodes['Sum of Neighbours'] = sum_neighbours

In [42]:
# add sum of neighbours and sum of papers to pairs_df
neighbours = []
papers =[]
for i, row in pairs_df.iterrows():
    temp = nodes.loc[(nodes['Node'] == row['Node1'])|(nodes['Node'] == row['Node2'])]
    neighbours.append(temp['Sum of Neighbours'].sum())
    papers.append(temp['Sum of Papers'].sum())

In [43]:
pairs_df['Sum of Neighbours'] = neighbours
pairs_df['Sum of Papers'] = papers

### Feature: Shortest Distance

In [44]:
pairs_df.columns

Index(['Node1', 'Node2', 'y', 'Sum of Neighbours', 'Sum of Papers'], dtype='object')

In [45]:
shortest_distance = [] 
second_shortest_distance = []
for i, row in pairs_df.iterrows():
    try:
        done = False
        X = nx.shortest_simple_paths(train_g, row['Node1'], row['Node2'])
        for counter, path in enumerate(X):
            if counter == 0: 
                shortest_distance.append(len(path))
            elif counter == 1: 
                second_shortest_distance.append(len(path))
                done = True
            else:
                break
        if not done: 
            second_shortest_distance.append(np.inf)
    except nx.NetworkXNoPath:
        shortest_distance.append(np.inf)
        second_shortest_distance.append(np.inf)

In [46]:
pairs_df['shortest distance'] = shortest_distance
pairs_df['second shortest distance'] = second_shortest_distance

# Sampling Approaches

In [47]:
pairs_df['y'].value_counts()

False    292974
True       1554
Name: y, dtype: int64

In [51]:
## Random Undersampling
import random
random.seed(42)
neg_indices = pairs_df.loc[pairs_df['y']== False].index.to_list()
neg_sample = random.sample(neg_indices, 1554)
pairs_df_sample = pairs_df.loc[neg_sample]
pairs_df_sample = pd.concat([pairs_df_sample, pairs_df.loc[pairs_df['y']== True]])

In [52]:
#neighbourhood sampling
pairs_df_neighbourhood = pairs_df.loc[pairs_df['shortest distance'] == 3]

In [53]:
pairs_df_neighbourhood['y'].value_counts()

False    4865
True       18
Name: y, dtype: int64

# Classifiers
### Dummy

In [66]:
def dummy(x):
    avg_acc = []; avg_precision =[]; avg_recall = []; avg_f1 = []; avg_auc = []
    for seed in [0,1,2,3,4]:
        acc =[]; precision = []; recall = []; f1 = []; auc = []
        cv = model_selection.StratifiedKFold(n_splits=5, shuffle = True, random_state = seed)
        for train_index, test_index in cv.split(x, x['y']):
            x_tr, x_te = x.iloc[train_index], x.iloc[test_index]
            if x_tr.loc[x_tr['y']==1,'y'].shape[0] <=  x_tr.loc[x_tr['y']==0,'y'].shape[0]:
                majority_class = 0
            else: 
                majority_class = 1
            print('majority class: ', majority_class)
            y_pred = [majority_class for i in range(len(x_te['y']))]
            y_te = x_te['y'].tolist()


            acc.append(metrics.accuracy_score(y_te, y_pred))
            precision.append(metrics.precision_score(y_te, y_pred))
            recall.append(metrics.recall_score(y_te, y_pred))
            f1.append(metrics.f1_score(y_te, y_pred))
            auc.append(metrics.roc_auc_score(y_te, y_pred))
        avg_acc.append(np.mean(acc))
        avg_precision.append(np.mean(precision))
        avg_recall.append(np.mean(recall))
        avg_f1.append(np.mean(f1))
        avg_auc.append(np.mean(auc))
    print('acc', avg_acc, np.mean(avg_acc))
    print('precision',avg_precision,  np.mean(avg_precision))
    print('recall',avg_recall, np.mean(avg_recall))
    print('f1', avg_f1,  np.mean(avg_f1))
    print('AUC',avg_auc, np.mean(avg_auc))

#%%


In [67]:
dummy(pairs_df[['Node1','Node2', 'y']])

majority class:  0
majority class:  0


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


majority class:  0


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


majority class:  0


...

C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


 0
majority class:  0
majority class:  0


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


majority class:  0
acc [0.994723761442302, 0.994723761442302, 0.994723761442302, 0.994723761442302, 0.994723761442302] 0.994723761442302
precision [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
recall [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
f1 [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
AUC [0.5, 0.5, 0.5, 0.5, 0.5] 0.5


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [85]:
dummy(pairs_df_sample[['Node1','Node2', 'y']])

majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
majority class:  1
acc [0.5012835946824711, 0.5012835946824711, 0.5012835946824711, 0.5012835946824711, 0.5012835946824711] 0.5012835946824711
precision [0.5012835946824711, 0.5012835946824711, 0.5012835946824711, 0.5012835946824711, 0.5012835946824711] 0.5012835946824711
recall [1.0, 1.0, 1.0, 1.0, 1.0] 1.0
f1 [0.6678064208097482, 0.6678064208097482, 0.6678064208097482, 0.6678064208097482, 0.6678064208097482] 0.6678064208097482
AUC [0.5, 0.5, 0.5, 0.5, 0.5] 0.5


In [104]:
dummy(pairs_df_neighbourhood[['Node1','Node2', 'y']])

majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class: 

C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision 

 0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
majority class:  0
acc [0.9963139923150495, 0.9963139923150495, 0.9963139923150495, 0.9963139923150495, 0.9963139923150495] 0.9963139923150495
precision [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
recall [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
f1 [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
AUC [0.5, 0.5, 0.5, 0.5, 0.5] 0.5


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision 

### Jaccard Similarity

In [64]:
def jaccard(x, threshold = 0.5, jaccard = None, verbose = True):
    avg_acc = []; avg_precision =[]; avg_recall = []; avg_f1 = []; avg_auc = []

    for seed in [0,1,2,3,4]:
        #print('seed', seed)
        acc =[]; precision = []; recall = []; f1 = []; auc = []
        cv = model_selection.StratifiedKFold(n_splits=5, shuffle = True, random_state = seed)
        for train_index, test_index in cv.split(x,x['y']):
            x_tr, x_te = x.iloc[train_index], x.iloc[test_index]
            y_pred = []
            y_te = []
            for i, row in x_te.iterrows(): 
                if (row['Node1'], row['Node2']) in jaccard.keys():
                    key = (row['Node1'], row['Node2'])
                else: 
                    key = (row['Node2'], row['Node1'])
                if jaccard[key] < threshold:
                    y_pred.append(0)
                else: 
                    y_pred.append(1)
                y_te.append(row['y'])
            acc.append(metrics.accuracy_score(y_te, y_pred))
            precision.append(metrics.precision_score(y_te, y_pred))
            recall.append(metrics.recall_score(y_te, y_pred))
            f1.append(metrics.f1_score(y_te, y_pred))
            auc.append(metrics.roc_auc_score(y_te, y_pred))
        avg_acc.append(np.mean(acc))
        avg_precision.append(np.mean(precision))
        avg_recall.append(np.mean(recall))
        avg_f1.append(np.mean(f1))
        avg_auc.append(np.mean(auc))
    if verbose:
        print('acc', avg_acc, np.mean(avg_acc))
        print('precision',avg_precision,  np.mean(avg_precision))
        print('recall',avg_recall, np.mean(avg_recall))
        print('f1', avg_f1,  np.mean(avg_f1))
        print('AUC',avg_auc, np.mean(avg_auc))
    else:
        print('acc',np.mean(avg_acc))
        print('precision',np.mean(avg_precision))
        print('recall',np.mean(avg_recall))
        print('f1', np.mean(avg_f1))
        print('AUC',np.mean(avg_auc))  


In [ ]:
pairs_df['jtuple'] = list(zip(pairs_df.Node1, pairs_df.Node2))
jaccard_similarity = list(nx.jaccard_coefficient(g, pairs_df['jtuple'].tolist()))

In [89]:
pairs_df_sample['jtuple'] = list(zip(pairs_df_sample.Node1, pairs_df_sample.Node2))
jaccard_similarity = list(nx.jaccard_coefficient(g, pairs_df_sample['jtuple'].tolist()))

In [105]:
pairs_df_neighbourhood['jtuple'] = list(zip(pairs_df_neighbourhood.Node1, pairs_df_neighbourhood.Node2))
jaccard_similarity = list(nx.jaccard_coefficient(g, pairs_df_neighbourhood['jtuple'].tolist()))

<ipython-input-105-dd2920721f23>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pairs_df_neighbourhood['jtuple'] = list(zip(pairs_df_neighbourhood.Node1, pairs_df_neighbourhood.Node2))


In [106]:
jaccard_dict= {}
for j in list(jaccard_similarity):
    jaccard_dict[(j[0], j[1])] = j[2]

In [107]:
jaccard(pairs_df_neighbourhood[['Node1','Node2', 'y']],jaccard= jaccard_dict,threshold = 0.1)

acc [0.3594115475611188, 0.35940777220329884, 0.3594056747822877, 0.3594109183348155, 0.3594163716294444] 0.3594104569021931
precision [0.004780790041557043, 0.0047887405259101476, 0.004794036130224465, 0.004780272054168202, 0.004772611298299148] 0.004783290010031802
recall [0.8333333333333334, 0.8166666666666667, 0.85, 0.8333333333333333, 0.85] 0.8366666666666666
f1 [0.009506123623559515, 0.009520660278234672, 0.009532953911950007, 0.009504987337275667, 0.0094911438333127] 0.009511173796866512
AUC [0.5954950325453923, 0.587161699212059, 0.6038283658787255, 0.5954950325453923, 0.6038283658787256] 0.597161699212059


In [101]:
for i in [0,0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9,1]:
    print(i)
    jaccard(pairs_df_sample[['Node1','Node2', 'y']],jaccard = jaccard_dict, threshold = i, verbose =False)


0
acc 0.5012835946824711
precision 0.5012835946824711
recall 1.0
f1 0.6678064208097482
AUC 0.5
0.1
acc 0.8324775692472324
precision 0.9914684044563797
recall 0.6715769640370279
f1 0.800575622786613
AUC 0.8328923094223104
0.2
acc 0.7426180186854344
precision 0.9948597146900209
recall 0.48912427295813876
f1 0.6553408278690683
AUC 0.7432749256088277
0.3
acc 0.6768288266041075
precision 0.9928935357268059
recall 0.3578819529777996
f1 0.5257470924723336
AUC 0.6776537656186582
0.4
acc 0.6296527349055439
precision 0.9952982002876929
recall 0.26248750716801833
f1 0.4150489598477155
AUC 0.6306004593199287
0.5
acc 0.5998075894143311
precision 0.9938674644188119
recall 0.20295076595396083
f1 0.33680033584682423
AUC 0.6008320887129
0.6
acc 0.5455710581553278
precision 0.987408875755278
recall 0.094750143360367
f1 0.17258794472129138
AUC 0.546731777416103
0.7
acc 0.5166882742725439
precision 0.9685359477124184
recall 0.03713197345785206
f1 0.07140707340864967
AUC 0.5179226924648455
0.8


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


acc 0.5006420545746388
precision 0.7566666666666666
recall 0.00512124191037929
f1 0.010162846053650582
AUC 0.5019173266911091
0.9


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision 

acc 0.49839558381693216
precision 0.2
recall 0.0006406160399770623
f1 0.0012771412873160905
AUC 0.499677013755908
1


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision 

acc 0.4980746594229741
precision 0.0
recall 0.0
f1 0.0
AUC 0.4993567057359195


### Node2Vec Classifier
Implementation from https://stellargraph.readthedocs.io/en/stable/demos/link-prediction/node2vec-link-prediction.html. This code is merely altered for my purpose.

In [92]:

from stellargraph import StellarGraph, datasets
from stellargraph.data import EdgeSplitter
from stellargraph.data import BiasedRandomWalk
from gensim.models import Word2Vec
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegressionCV, LogisticRegression
from sklearn.metrics import roc_auc_score
from sklearn.preprocessing import StandardScaler
import multiprocessing

In [133]:
def node2vec_embedding(graph, name):
    p = 1.0
    q = 1.0
    dimensions = 128
    num_walks = 10
    walk_length = 80
    window_size = 10
    num_iter = 1
    workers = multiprocessing.cpu_count()
    rw = BiasedRandomWalk(graph)
    walks = rw.run(graph.nodes(), n=num_walks, length=walk_length, p=p, q=q)
    print(f"Number of random walks for '{name}': {len(walks)}")

    model = Word2Vec(
        walks,
        size=dimensions,
        window=window_size,
        min_count=0,
        sg=1,
        workers=workers,
        iter=num_iter,
    )

    def get_embedding(u):
        return model.wv[u]

    return get_embedding


# 1. link embeddings
def link_examples_to_features(link_examples, transform_node, binary_operator):
    return [
        binary_operator(transform_node(src), transform_node(dst))
        for src, dst in link_examples
    ]


# 2. training classifier
def train_link_prediction_model(
    link_examples, link_labels, get_embedding, binary_operator, seed
):
    clf = link_prediction_classifier(seed)
    link_features = link_examples_to_features(
        link_examples, get_embedding, binary_operator
    )
    clf.fit(link_features, link_labels)
    return clf


def link_prediction_classifier(seed, max_iter=2000):
    lr_clf = LogisticRegression(C=10, max_iter=max_iter, random_state = seed)
    #LogisticRegressionCV(Cs=10, cv=3, scoring="roc_auc", max_iter=max_iter, random_state = seed)
    return Pipeline(steps=[("sc", StandardScaler()), ("clf", lr_clf)])


# 3. and 4. evaluate classifier
def evaluate_link_prediction_model(
    clf, link_examples_test, link_labels_test, get_embedding, binary_operator
):
    link_features_test = link_examples_to_features(
        link_examples_test, get_embedding, binary_operator
    )
    score = evaluate_roc_auc(clf, link_features_test, link_labels_test)
    return score


def evaluate_roc_auc(clf, link_features, link_labels):
    predicted = clf.predict(link_features)
    return metrics.accuracy_score(link_labels, predicted), metrics.precision_score(link_labels, predicted), metrics.recall_score(link_labels, predicted),metrics.f1_score(link_labels, predicted), metrics.roc_auc_score(link_labels, predicted)


#%%

def operator_hadamard(u, v):
    return u * v


def operator_l1(u, v):
    return np.abs(u - v)


def operator_l2(u, v):
    return (u - v) ** 2


def operator_avg(u, v):
    return (u + v) / 2.0


#%%

def node2vec(x, seed = 42): 
    # get training
    edges = train_df[['Source', 'Target']]
    edges = edges.rename(columns = {'Source':'source', 'Target':'target'})
    train_graph = StellarGraph(edges=edges)
    print(train_graph.info())
    
    # test graph: ever needed? 
    #edges = edges_df[['Node1', 'Node2', 'Occurances']]
    #edges = edges.rename(columns = {'Node1':'source', 'Node2':'target', 'Occurances': 'weight'})
    #test_graph = StellarGraph(edges=edges)
    #print(test_graph.info())
    


    embedding_train = node2vec_embedding(train_graph, "train")
    
    
    y = pairs_df_neighbourhood['y']
    
    
    print('starting cv')
           
    for binary_operator in  [operator_hadamard, operator_l1, operator_l2, operator_avg]: 
        avg_acc = []; avg_precision =[]; avg_recall = []; avg_f1 = []; avg_auc = []
        for seed in [0,1,2,3,4]:
            cv = model_selection.StratifiedKFold(n_splits=2, shuffle = True, random_state = seed) 
            for train_index, test_index in cv.split(x,y):
                acc =[]; precision =[]; recall = []; f1 =[]; auc = []
                index = random.sample(x.index.to_list(), int(len(x)/5))
                y_tr = y.iloc[train_index].to_numpy()
                x_tr = x.iloc[train_index].to_numpy()
                y_te = y.iloc[test_index].to_numpy()
                x_te = x.iloc[test_index].to_numpy()

                clf = train_link_prediction_model(x_tr,y_tr, embedding_train, binary_operator,seed)
                a, p, r, f, ac = evaluate_link_prediction_model(clf,x_te,y_te,embedding_train,binary_operator)

                acc.append(a)
                precision.append(p)
                recall.append(r)
                f1.append(f)
                auc.append(ac)
            avg_acc.append(np.mean(acc))
            avg_precision.append(np.mean(precision))
            avg_recall.append(np.mean(recall))
            avg_f1.append(np.mean(f1))
            avg_auc.append(np.mean(auc))
            
        print('---')
        print(binary_operator.__name__)
        print('acc', avg_acc, np.mean(avg_acc))
        print('precision',avg_precision,  np.mean(avg_precision))
        print('recall',avg_recall, np.mean(avg_recall))
        print('f1', avg_f1,  np.mean(avg_f1))
        print('AUC',avg_auc, np.mean(avg_auc))



In [130]:
node2vec(pairs_df[['Node1', 'Node2']], 42)

StellarGraph: Undirected multigraph
 Nodes: 768, Edges: 1464

 Node types:
  default: [768]
    Features: none
    Edge types: default-default->default

 Edge types:
    default-default->default: [1464]
        Weights: all 1 (default)
        Features: none
Number of random walks for 'train': 7680
starting cv
---
operator_hadamard
acc [0.9960682855280313, 0.9961837244676228, 0.9961497718383312, 0.9959392655367232, 0.9961090286831812] 0.9960900152107779
precision [0.75, 0.7792207792207793, 0.7692307692307693, 0.7594202898550725, 0.7756756756756756] 0.7667095027964593
recall [0.38223938223938225, 0.3861003861003861, 0.3861003861003861, 0.33719433719433717, 0.36936936936936937] 0.3722007722007722
f1 [0.5063938618925833, 0.5163511187607575, 0.5141388174807198, 0.46702317290552586, 0.5004359197907584] 0.500868578166069
AUC [0.6907817771751089, 0.692760064915956, 0.6927429985551184, 0.6683138670072664, 0.6844013830947825] 0.6858000181496464
---
operator_l1
acc [0.9956744350282486, 0.9955046

C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision 

---
operator_avg
acc [0.9947237614080835, 0.9947237614080835, 0.9947237614080835, 0.9947237614080835, 0.9947237614080835] 0.9947237614080835
precision [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
recall [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
f1 [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
AUC [0.5, 0.5, 0.5, 0.5, 0.5] 0.5


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [132]:
node2vec(pairs_df_sample[['Node1', 'Node2']], 42)

StellarGraph: Undirected multigraph
 Nodes: 768, Edges: 1464

 Node types:
  default: [768]
    Features: none
    Edge types: default-default->default

 Edge types:
    default-default->default: [1464]
        Weights: all 1 (default)
        Features: none
Number of random walks for 'train': 7680
starting cv
---
operator_hadamard
acc [0.9159178433889602, 0.9313222079589217, 0.9249037227214377, 0.9184852374839538, 0.9338896020539152] 0.9249037227214376
precision [0.8982843137254902, 0.9160493827160494, 0.9191919191919192, 0.9057071960297767, 0.9226932668329177] 0.9123852156992307
recall [0.93854033290653, 0.9500640204865557, 0.9321382842509603, 0.9346991037131882, 0.9475032010243278] 0.9405889884763126
f1 [0.9179711959924858, 0.9327467001885608, 0.9256198347107438, 0.9199747952110902, 0.9349336702463678] 0.9262492392698498
AUC [0.9158596130427117, 0.9312739664852341, 0.9248851009414389, 0.9184435029505452, 0.933854560615124] 0.9248633488070108
---
operator_l1
acc [0.9127086007702182, 

In [134]:
node2vec(pairs_df_neighbourhood[['Node1', 'Node2']], 42)

StellarGraph: Undirected multigraph
 Nodes: 768, Edges: 1464

 Node types:
  default: [768]
    Features: none
    Edge types: default-default->default

 Edge types:
    default-default->default: [1464]
        Weights: all 1 (default)
        Features: none
Number of random walks for 'train': 7680
starting cv
---
operator_hadamard
acc [0.9950839819746006, 0.9959033183121672, 0.994264645637034, 0.9938549774682507, 0.9954936501433839] 0.9949201147070873
precision [0.2, 0.4, 0.0, 0.0, 0.3333333333333333] 0.18666666666666668
recall [0.1111111111111111, 0.2222222222222222, 0.0, 0.0, 0.2222222222222222] 0.11111111111111112
f1 [0.14285714285714285, 0.2857142857142857, 0.0, 0.0, 0.26666666666666666] 0.13904761904761903
AUC [0.5547331871345029, 0.6104943347953217, 0.49897203947368424, 0.4987664473684211, 0.6102887426900585] 0.5546509502923976
---
operator_l1
acc [0.9963129864809505, 0.9954936501433839, 0.9946743138058173, 0.9950839819746006, 0.9950839819746006] 0.9953297828758705
precision [0.

### Bagging

In [54]:
### Bagging

from sklearn import model_selection
from sklearn import metrics


#%%

def bagging(x,y):
    avg_acc = []; avg_precision =[]; avg_recall = []; avg_f1 = []; avg_auc = []
    
    x = x.replace(np.inf, -1)
    for seed in [0,1,2,3,4]:
        acc =[]; precision = []; recall = []; f1 = []; auc = []
        cv = model_selection.StratifiedKFold(n_splits=5, shuffle = True, random_state = seed)
        clf =BaggingClassifier( n_estimators=10, random_state=42)
        for train_index, test_index in cv.split(x, y):
            x_tr, x_te = x.iloc[train_index], x.iloc[test_index]
            y_tr, y_te = y.iloc[train_index], y.iloc[test_index]
            clf.fit(x_tr, y_tr)
            y_pred = clf.predict(x_te)
            acc.append(metrics.accuracy_score(y_te, y_pred))
            precision.append(metrics.precision_score(y_te, y_pred))
            recall.append(metrics.recall_score(y_te, y_pred))
            f1.append(metrics.f1_score(y_te, y_pred))
            auc.append(metrics.roc_auc_score(y_te, y_pred))

        avg_acc.append(np.mean(acc))
        avg_precision.append(np.mean(precision))
        avg_recall.append(np.mean(recall))
        avg_f1.append(np.mean(f1))
        avg_auc.append(np.mean(auc))
        
    print('acc', avg_acc, np.mean(avg_acc))
    print('precision',avg_precision,  np.mean(avg_precision))
    print('recall',avg_recall, np.mean(avg_recall))
    print('f1', avg_f1,  np.mean(avg_f1))
    print('AUC',avg_auc, np.mean(avg_auc))


In [121]:
x = pairs_df[['Sum of Neighbours', 'Sum of Papers', 'shortest distance', 'second shortest distance']]
y = pairs_df['y']
x = x.replace(np.inf, -1)
bagging(x,y)

acc [0.9996774497335112, 0.9996944260481581, 0.9996842403285371, 0.9996842408472901, 0.9996910308082845] 0.9996862775531561
precision [0.9966116008062317, 1.0, 0.9979522184300341, 0.9979840728100114, 0.9993103448275862] 0.9983716473747727
recall [0.9420703246551188, 0.942084845970335, 0.9420869204439374, 0.9420786225495279, 0.942084845970335] 0.9420811119178509
f1 [0.9685337497902993, 0.970126151437617, 0.9692044595062773, 0.9691303267874986, 0.9698167510944959] 0.9693622877232377
AUC [0.9710266291471402, 0.9710424229851673, 0.971038340243814, 0.9710341913839884, 0.9710407163257825] 0.9710364600171785


In [120]:
x = pairs_df_sample[['Sum of Neighbours', 'Sum of Papers', 'shortest distance', 'second shortest distance']]
y = pairs_df_sample['y']
x = x.replace(np.inf, -1)
bagging(x,y)

acc [0.9698316664608798, 0.9669460221426514, 0.9685521875128617, 0.9688675556653085, 0.9663044820348192] 0.9681003827633041
precision [0.988064813212536, 0.9841274409073175, 0.9861222319757414, 0.9873301878699191, 0.9815401277538734] 0.9854369603438775
recall [0.951343491439338, 0.9494327025477187, 0.9507188498402556, 0.9500491521258294, 0.950712705824527] 0.9504513803555337
f1 [0.9693292500057721, 0.9664277605423297, 0.968025448491173, 0.968316408025528, 0.9658498420410148] 0.9675897418211635
AUC [0.969878778185181, 0.9669961977628126, 0.9686049388709629, 0.9689121395936688, 0.9663500257677764] 0.9681484160360803


In [119]:
x = pairs_df_neighbourhood[['Sum of Neighbours', 'Sum of Papers', 'shortest distance', 'second shortest distance']]
y = pairs_df_neighbourhood['y']
x = x.replace(np.inf, -1)
bagging(x,y)

C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision 

acc [0.995699867442992, 0.9956996577008909, 0.995699657700891, 0.9952898216353171, 0.9954949494102052] 0.9955767907780592
precision [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
recall [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
f1 [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
AUC [0.4996916752312436, 0.4996916752312436, 0.4996916752312435, 0.499486125385406, 0.49958890030832476] 0.49963001027749226


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


### Singular Value Decomposition

In [135]:
from surprise import SVD
from surprise import Dataset
from surprise import Reader
from surprise.model_selection import cross_validate
from surprise.model_selection import KFold

#%%

def svd(x):
    avg_acc = []; avg_precision =[]; avg_recall = []; avg_f1 = []; avg_auc = []
    
    
    algo = SVD()
    reader = Reader(rating_scale=(0,1))
    for seed in [0,1,2,3,4]:
        acc =[]; precision = []; recall = []; f1 = []; auc = []
        cv = model_selection.KFold(n_splits=5, shuffle = True, random_state = seed)
        accuracy = []
        # define a cross-validation iterator
        #kf = KFold(n_splits=5, random_state =42)
        cv = model_selection.StratifiedKFold(n_splits=5, shuffle = True, random_state = seed)
        algo = SVD()
        for train_index, test_index in cv.split(x,x['y']):
        # The columns must correspond to user id, item id and ratings (in that order).
            x_tr, x_te = x.iloc[train_index], x.iloc[test_index]
            trainset = Dataset.load_from_df(x_tr, reader)
            testset = Dataset.load_from_df(x_te, reader)
        #for trainset, testset in kf.split(data):

            # train and test algorithm.
            trainset = trainset.build_full_trainset()
            algo.fit(trainset)
            testset = testset.build_full_trainset().build_testset()
            predictions = algo.test(testset)
            y_te = []; y_pred = []
            for p in range(len(predictions)):
                y_te.append(testset[p][2])
                if predictions[p].est <= 0.5:
                    y_pred.append(0)
                else:
                    y_pred.append(1)
            acc.append(metrics.accuracy_score(y_te, y_pred))
            precision.append(metrics.precision_score(y_te, y_pred))
            recall.append(metrics.recall_score(y_te, y_pred))
            f1.append(metrics.f1_score(y_te, y_pred))
            auc.append(metrics.roc_auc_score(y_te, y_pred))
        avg_acc.append(np.mean(acc))
        avg_precision.append(np.mean(precision))
        avg_recall.append(np.mean(recall))
        avg_f1.append(np.mean(f1))
        avg_auc.append(np.mean(auc))
        
    print('acc', avg_acc, np.mean(avg_acc))
    print('precision',avg_precision,  np.mean(avg_precision))
    print('recall',avg_recall, np.mean(avg_recall))
    print('f1', avg_f1,  np.mean(avg_f1))
    print('AUC',avg_auc, np.mean(avg_auc))

In [136]:
svd(pairs_df[['Node1', 'Node2', 'y']])


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision 

acc [0.994723761442302, 0.994723761442302, 0.994723761442302, 0.994723761442302, 0.994723761442302] 0.994723761442302
precision [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
recall [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
f1 [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
AUC [0.5, 0.5, 0.5, 0.5, 0.5] 0.5


In [137]:
svd(pairs_df_sample[['Node1', 'Node2', 'y']])


acc [0.6100799481417459, 0.6248389718895335, 0.6241994896489278, 0.6004419269868707, 0.6126455941062683] 0.6144411861546692
precision [0.6059362343387552, 0.6173933258439119, 0.6170609950347412, 0.5963636103659543, 0.6090578936135487] 0.6091624118393822
recall [0.6350864258212501, 0.6638772835258457, 0.6587634144343409, 0.6292946669943476, 0.6350823298107643] 0.6444208241173097
f1 [0.6200009247238395, 0.6396837643503271, 0.6371448441893058, 0.6122787246371165, 0.6216074230274984] 0.6261431361856175
AUC [0.610019097154998, 0.6247474790204688, 0.624106320846462, 0.6003604337979723, 0.6125914708902385] 0.614364960342028


In [138]:
svd(pairs_df_neighbourhood[['Node1', 'Node2', 'y']])


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision 

acc [0.9963139923150495, 0.9963139923150495, 0.9963139923150495, 0.9963139923150495, 0.9963139923150495] 0.9963139923150495
precision [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
recall [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
f1 [0.0, 0.0, 0.0, 0.0, 0.0] 0.0
AUC [0.5, 0.5, 0.5, 0.5, 0.5] 0.5


C:\Users\thale\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
